## Visualizing results -  Spacy + en + georesolver

### Loading the necessary libraries

In [6]:
import yaml
from IPython.core.display import display, HTML
import pandas as pd 
import matplotlib.pyplot as plt
import numpy as np

### Functions

In [7]:
def read_query_results(filename):
    with open('./results_Gazetteer/'+filename, 'r') as f:
        query_results = yaml.load(f)
    return query_results


In [8]:
def display_spacy_entities(result):
    for i in result.keys():
        for k in result[i]:
            html= k["display_doc"]
            if html:
                print(" \n ----- %s: Entities with the Spacy \"%s\" language model  ----- \n" % (k["text_unit id"], k["lang_model"]))
                display(HTML(html))

In [9]:
def display_geoparser_entities(result):
    for i in result.keys():
        for k in result[i][0:15]:
            ER= k["display_ER"]
            print(" %s -- Clean Text: %s \n" %( k["text_unit id"], k["clean_text"]))
            if ER:
                print(" --> \t %s -- Entities with the Original Geoparser: \n" % k["text_unit id"])
                for ent in ER[2:]:
                    print("%s (p:%s, group:%s)" %(ent[0], ent[1]["p"], ent[1]["group"]), end='', flush=True)
                print("\n")
         

In [10]:
def geresolution_dataframe(result):
    dfs=[]
    data=[]
    c_locs=[]
    for i in result.keys():
        t_ind = 0
        e_ind = 0
        for k in result[i]:
            locs= k["georesolution_page"]
            page = k["text_unit id"]
       
            if locs != {}:
                data=[]
                l_ind = 0
                for i in locs:
                    if type(locs[i]) == type([]) :
                        c_locs=locs[i].copy()
                        c_locs.append(i.split("-")[0])
                        c_locs.append(page)
                        data.append(c_locs)
                        l_ind = l_ind + 1   
                e_ind = t_ind + l_ind 
                if data:
                    df_page = pd.DataFrame(data, columns = ['Latitude', 'Longitude', 'Place', 'Page'], 
                                      index=list(range(t_ind, e_ind)))
                    dfs.append(df_page)
                    t_ind=e_ind
    df_total = pd.concat(dfs)
    return df_total


We run the *georesolution_pages* defoe query over "Descriptive account of the principal towns in Scotland - 1828"* gazetter using the "en" model (specified in queries/lang_model.yml file) 

    spark-submit --py-files defoe.zip defoe/run_query.py nls-gaz-demo.txt nls defoe.nls.queries.georesolution_pages  queries/lang_model.yml -r georesolution_97350713_en -n 16
 
Note: We just perfomed this study using all the pages of one book. Therefore, the *nlz-gaz-demo.txt* only has one directory: XXXX/nls-data-gazetteersOfScotland/97350713. But we could run this query using the full dataset (which will include all the directories).

This query does the following tasks:

- Ingests all the pages from the directory "97350713",  which corresponds to the book "Descriptive account of the principal towns in Scotland - 1828"
- Cleans the text applied two fixes: Long-s and hyphen words
- Identifies *entities* running spacy over the cleaned text using the language model specified in lang_model.yml ("en" | "en_core_web_lg")
- From the previous entities, just selects the one about *location* (GPE, LOC) and creates an xml (in memory) per page with these "location" entities. 
- Applies the georesolve (from the Edinburgh Geoparser) to each xml and gets lat and long. 
- Group the results by Book's title, and also gets some informative metadata

As a result we get a file per gazetter|book with an entry per page with the following information:

    * archive_filename: Path to the gazetteer 
    * clean_text: Page's clean text after applying 2 fixes: long-S and hyphenate words
    * display_doc: Display of a page’s entities found by SpaCy (in HTML format)
    * edition: Edition of the gazetteer
    * georesolution_page: Page's geolocations after applying the georesolver to the page’s  locations (GPE|LOC) found by SpaCy
    * model: defoe model – could be fmp|nls|papers|alto. In this case is “nls”
    * text_unit: page (for other defoe models could be “article”)
    * num_text_unit: number of tex units. In this case, number of pages of this particular gazetter (e.g. 376)
    * page_filename: Page's filename (page's relative path)
    * text_unit id: The number of this page (e.g. Page 1)
    * lang_model : The language model applied (en | en_core_web_lg )
    * type_distribution: type of document (newspaper|book). In this case is "book". 
    * year: Gazetter's year 


Example:

    - "Descriptive account of the principal towns in Scotland: to accompany Wood''s town atlas':
        - archive_filename: /home/tdm/datasets/nls-data-gazetteersOfScotland/97350713
          clean_text: "Xll Greenock, 171 Haddington, 181 Hamilton, ..."
          display_doc: "<div class=\"entities\" ... </div>"
          edition: '1828'
          georesolution_page:
              Hamilton-1:
                - '55.77731433348086'
                - '-4.067392672500774'
              Inverary-2:
                - '56.2333333'
                - '-5.0666667'
              Inverness-3:
                - '57.47871409771949'
                - '-4.212450527351024'
              Lanark-4:
                - '55.67483195471274'
                - '-3.775417694605498'
              lang_model: en
              model: nls
              num_text_unit: 376
              page_filename: alto/97350923.34.xml
              place: Edinburgh
              text_unit: page
              text_unit id: Page18
              type_distribution: book
              year: 1828


In [11]:
results=read_query_results('georesolution_97350713_en')

In [12]:
display_spacy_entities(results)

 
 ----- Page2: Entities with the Spacy "en" language model  ----- 



 
 ----- Page3: Entities with the Spacy "en" language model  ----- 



 
 ----- Page4: Entities with the Spacy "en" language model  ----- 



 
 ----- Page7: Entities with the Spacy "en" language model  ----- 



 
 ----- Page9: Entities with the Spacy "en" language model  ----- 



...

 
 ----- Page365: Entities with the Spacy "en" language model  ----- 



 
 ----- Page367: Entities with the Spacy "en" language model  ----- 



 
 ----- Page368: Entities with the Spacy "en" language model  ----- 



 
 ----- Page369: Entities with the Spacy "en" language model  ----- 



 
 ----- Page370: Entities with the Spacy "en" language model  ----- 



In [13]:
df_total= geresolution_dataframe(results)

In [14]:
df_total

Latitude            Longitude           Place     Page
0           50.333333655        -57.531547279           Bound    Page7
1      57.68633318560074    -4.96890721218449        Scotland    Page9
2      63.08985016483783   -113.2169083324163          Gordon   Page13
3             55.6166667           -3.4166667       Broughton   Page14
4      56.14619703287505   -3.216735886949388           Cluny   Page14
5      56.47018024186861    -3.16215196256474         Hillton   Page14
6      55.77731433348086   -4.067392672500774        Hamilton   Page18
7      57.47871409771949   -4.212450527351024       Inverness   Page18
8      55.67483195471274   -3.775417694605498          Lanark   Page18
9             56.2333333           -5.0666667        Inverary   Page18
10     51.46269887944979  0.04732822032113404       Greenwich   Page23
11            42.7737033          -70.8411626             Old   Page23
12            42.7737033          -70.8411626        Old Town   Page23
13      52.1412992458346   0.6363058597995664      Gallowgate   Page24
14     57.15956045188484   -2.134722052407824        Aberdeen   Page25
15     57.15956045188484   -2.134722052407824        Aberdeen   Page25
16     57.68633318560074    -4.96890721218449        Scotland   Page25
17      55.9251525946208   -3.284768133955424       Edinburgh   Page27
18     57.15956045188484   -2.134722052407824        Aberdeen   Page27
19     57.15956045188484   -2.134722052407824        Aberdeen   Page27
20     57.68633318560074    -4.96890721218449        Scotland   Page27
21     57.15956045188484   -2.134722052407824        Aberdeen   Page28
22      57.1673146280548   -2.092580471298619    Old Aberdeen   Page28
23     57.15956045188484   -2.134722052407824        Aberdeen   Page28
24             35.095046         -106.6708594    the Old Town   Page28
25     57.15956045188484   -2.134722052407824        Aberdeen   Page29
26     57.15956045188484   -2.134722052407824        Aberdeen   Page29
27     57.15956045188484   -2.134722052407824        Aberdeen   Page29
28            44.6436613   -72.83068350000001    the Old Town   Page30
29     57.68633318560074    -4.96890721218449        Scotland   Page30
...                  ...                  ...             ...      ...
1094    55.9251525946208   -3.284768133955424       Edinburgh  Page361
1095   57.15956045188484   -2.134722052407824        Aberdeen  Page361
1096   56.86975802114635   -2.534745750336879      Kincardine  Page361
1097            51.59468             -1.12829  the south east  Page361
1098   56.42282247580768    -3.47920071045354           Perth  Page361
1099   56.70832370552517   -2.467117965467635        Montrose  Page361
1100          41.5289871          -72.0786883            Jail  Page362
1101   56.96590381553843    -2.21754202999286      Stonehaven  Page362
1102   57.15956045188484   -2.134722052407824        Aberdeen  Page363
1103           39.521218          -76.4271849      Strathmore  Page363
1104   57.68633318560074    -4.96890721218449        Scotland  Page363
1105            40.43579   -79.99572999999999     Magistrates  Page363
1106          16.8333333   -88.33333330000001         Regalia  Page364
1107          17.5666667          -88.5166667        Scotland  Page364
1108        44.816803279   -79.86636222600001       Candlemas  Page365
1109   57.33597195059147   -2.500225160021933            Urie  Page365
1110       -43.968337882        171.870109343       Stornaway  Page367
1111   45.26764557499408   -79.08598792226002            Bays  Page368
1112   53.69180622064813   -2.423529257645026        Scotland  Page368
1113           47.080374         -122.8459707       South Bay  Page369
1114        50.599615774       -126.686364102         Harbour  Page369
1115       -43.968337882        171.870109343       Stornaway  Page369
1116   58.24568165804411   -6.270516819262197       Broad Bay  Page369
1117  -16.90850249600256    145.7442102398504          Cairns  Page369
1118              47.438            -122

In [15]:
df_total[["Place"]].count()

Place    1124
dtype: int64

In [16]:
df_total.sum()

Latitude     50.33333365557.6863331856007463.08985016483783...
Longitude    -57.531547279-4.96890721218449-113.21690833241...
Place        BoundScotlandGordonBroughtonClunyHilltonHamilt...
Page         Page7Page9Page13Page14Page14Page14Page18Page18...
dtype: object

In [17]:
df_total.groupby("Place").count()

Latitude  Longitude  Page
Place                                                            
Aberdeen                                      24         24    24
Agnes                                          1          1     1
Aikman                                         1          1     1
Albany                                         3          3     3
Alnwick                                        1          1     1
America                                        8          8     8
Angus                                          3          3     3
Anstruther                                     1          1     1
Apparatus                                      1          1     1
Arbroath                                       2          2     2
Arran                                          5          5     5
Athol                                          1          1     1
Atlantic                                       2          2     2
Ayr                                            4          4     4
Ayrshire                                       1          1     1
Bailie                                         1          1     1
Balls                                          1          1     1
Baltic                                         1          1     1
Banff                                          1          1     1
Banffshire                                     1          1     1
Barony                                         4          4     4
Barracks                                       1          1     1
Basin                                          1          1     1
Baths                                          1          1     1
Bay                                            4          4     4
Bays                                           1          1     1
Beechwood                                      1          1     1
Bel mount                                      1          1     1
Belfast                                        1          1     1
Bervie                                         1          1     1
...                                          ...        ...   ...
Williamsburgh                                  1          1     1
Wooden                                         1          1     1
Wool                                           1          1     1
Writing                                        1          1     1
Yarrow                                         1          1     1
Yeomanry                                       1          1     1
dale                                           1          1     1
earth                                          1          1     1
east                                           5          5     5
hemp                                           1          1     1
hill                                           1          1     1
lichen                                         1          1     1
moss                                           1          1     1
north                                          2          2     2
north east                                     2          2     2
picturesque                                    1          1     1
sea coast                                      1          1     1
south                                          7          7     7
south east                                     1          1     1
the County Rooms,                              1          1     1
the County Rooms, Sheriff Court Rooms,         1          1     1
the Isle of Wight                              1          1     1
the Old Jail                                   1          1     1
the Old Town                                   3          3     3
the West Indies                                2          2     2
the east end                                   2          2     2
the south east                                 2          2     2
the west end                                   3          3     3
valley        

In [18]:
df_total.groupby("Page").count()

Latitude  Longitude  Place
Page                               
Page100         3          3      3
Page101         3          3      3
Page102         5          5      5
Page105         6          6      6
Page108         6          6      6
Page110         1          1      1
Page111         6          6      6
Page112         3          3      3
Page113         2          2      2
Page114         4          4      4
Page115         1          1      1
Page116         4          4      4
Page117         5          5      5
Page119         5          5      5
Page121         1          1      1
Page122         3          3      3
Page124         3          3      3
Page128         2          2      2
Page129         1          1      1
Page13          1          1      1
Page130         2          2      2
Page133        10         10     10
Page134         3          3      3
Page135         9          9      9
Page136         4          4      4
Page138         4          4      4
Page139         5          5      5
Page14          3          3      3
Page140         1          1      1
Page141        11         11     11
...           ...        ...    ...
Page68          9          9      9
Page69          1          1      1
Page7           1          1      1
Page70         13         13     13
Page71          7          7      7
Page72         11         11     11
Page73          3          3      3
Page75          7          7      7
Page76          5          5      5
Page77          2          2      2
Page79          2          2      2
Page80          1          1      1
Page81          1          1      1
Page82          5          5      5
Page83          1          1      1
Page84          2          2      2
Page85          7          7      7
Page86          4          4      4
Page87          1          1      1
Page88          2          2      2
Page89          1          1      1
Page9           1          1      1
Page90          2          2      2
Page91          1          1      1
Page92          8          8      8
Page94          3          3      3
Page96          6          6      6
Page97          3          3      3
Page98          3          3      3
Page99          4          4      4

[287 rows x 3 columns]